In [1]:
import sys
sys.path.append('../')

import torch
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset

import matplotlib.pyplot as plt
import numpy as np

from src.models.net import *
from src.si import *
from src.util import util as ut

/home/gmiglior/.conda/envs/stochint/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
mixed_dataloader, test_loader = ut.get_mixedloader_celeba_cartoon(batch_size=32, return_testloader=True)


Files already downloaded and verified


/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==14)
/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:34: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==11)
/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==14)
/

Datasets loaded
Concatenated


/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==14)
/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:34: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==11)
/home/gmiglior/cs274e/cs274e/notebooks/../src/util/util.py:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  labels[filename].append(row[1]==14)
/

In [3]:
class BigLatentClassifier(nn.Module):
    '''
    A bigger classifier for image data building a low-dimensional latent representation.
    '''
    def __init__(self, z_dim, ):
        super().__init__()
        self.z_dim = z_dim
        self.encoder = nn.Sequential(
                        nn.Conv2d(1, 64, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.BatchNorm2d(64),
                        nn.Conv2d(64, 64, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.MaxPool2d(kernel_size=2),

                        nn.Conv2d(64, 128, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.BatchNorm2d(128),
                        nn.Conv2d(128, 128, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.MaxPool2d(kernel_size=2),

                        nn.Conv2d(128, 256, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.BatchNorm2d(256),
                        nn.Conv2d(256, 256, kernel_size=3, padding=1),
                        nn.ReLU(),
                        nn.MaxPool2d(kernel_size=2),
                        
                        nn.Flatten(),
                        nn.Linear(256 * 64, z_dim*2),
                        nn.ReLU(),
                    )

        self.z_to_logits = nn.Sequential(
                        nn.Linear(z_dim, 32),
                        nn.ReLU(),
                        nn.Linear(32, 2),
                    )
        
    def forward(self, x):
        h = self.encoder(x)
        z_mu, z_sigma = ut.gaussian_parameters(h)
        z = z_mu + z_sigma * torch.randn_like(z_sigma)

        logits = self.z_to_logits(z)
        return logits, z_mu, z_sigma




In [8]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

betas = [0.01,]
lrs = [1e-3,]

best_accuracy = 10e5
best_loss = 10e5


for b in betas:
    for lr in lrs:
        classifier = BigLatentClassifier(z_dim=10).to(device)
        optimizer = optim.Adam(classifier.parameters(), lr=lr)

        classifier.train()
        for epoch in range(100):
            for i, batch in tqdm(enumerate(mixed_dataloader)):
                optimizer.zero_grad()
                batch_size = batch[0].shape[0]
                x, y = batch
                x = x.to(device)
                y = y.to(device).float()
                logits, z_mu, z_sigma = classifier(x)

                l = ut.compute_loss_BLC(logits, z_mu, z_sigma, y, beta=b)
                l.backward()
                optimizer.step()
            classifier.eval()
            test_loss = 0
            correct = 0.00
            with torch.no_grad():
                for i, batch in enumerate(test_loader):
                    x, y = batch
                    x = x.to(device)
                    y = y.to(device).float()

                    logits, z_mu, z_sigma = classifier(x)
                    test_loss += ut.compute_loss_BLC(logits, z_mu, z_sigma, y, beta=b).item()
                    prediction = torch.stack([i>0 for i in logits]).float()
                    is_correct = prediction == y
                    num_correct = torch.sum(is_correct)
                    correct += num_correct

            test_loss /= len(test_loader.dataset)
            correct /= 2*len(test_loader.dataset)
            print(f'Test set: Average loss: {test_loss:.4f}, Accuracy: {correct:.4f}')
        print(f"beta: {b}, lr: {lr}")
        print()

        if test_loss < best_loss:
            best_loss = test_loss
            best_accuracy = 100. * correct / len(test_loader.dataset)
            torch.save(classifier.state_dict(), f"../finetuning_scripts/classifier_celeba/celeba_beta_{b}_lr_{lr}.pt")

cuda


0it [00:00, ?it/s]


Test set: Average loss: 0.0203, Accuracy: 0.6773


0it [00:00, ?it/s]


Test set: Average loss: 0.0203, Accuracy: 0.6773


0it [00:00, ?it/s]


KeyboardInterrupt: 

In [6]:
torch.save(classifier.state_dict(), f"../finetuning_scripts/classifier_celeba/maximumlikelihood.pt")